In [1]:
import sys
import getpass
sys.path.append('..')

In [2]:
import pandas as pd
import os
import re
import time
from sqlalchemy import create_engine, text, inspect, MetaData, Table, Column, Integer, Float, String, Text, Boolean
from sqlalchemy.orm import sessionmaker
from sqlalchemy.ext.declarative import declarative_base
from geoalchemy2 import Geography, WKTElement
from FlowHandler import FlowHandler
from Akvo import Flow

In [3]:
PSQL_USER = getpass.getuser()
PSQL_PWD = os.environ['KEYCLOAK_PWD']
PSQL_DB = 'uduma'

In [4]:
instanceURI = 'udumamali'
requestURI = 'https://api.akvo.org/flow/orgs/' + instanceURI
surveysUrl = []

In [5]:
engine = create_engine("postgresql://{}:{}@localhost/{}".format(PSQL_USER, PSQL_PWD, PSQL_DB))
session = sessionmaker(bind=engine)()
getter = sessionmaker(bind=engine)()
Base = declarative_base()

## Helpers

In [6]:
then = time.time()

In [7]:
def getTime():
    now = time.time()
    decimal_time = int(( now - then)) / 60
    integer_time = int(decimal_time)
    seconds_time = decimal_time - integer_time
    seconds_time = int(60 * seconds_time)
    return '{} Minutes, {} Seconds'.format(integer_time, seconds_time)

## Classes

In [8]:
class Surveys(Base):
    
    __tablename__ = "survey"
    
    id = Column(Integer, primary_key=True)
    name = Column(Text)
    registration_id = Column(Integer, nullable=True)
    
    def __init__(self, data):
        self.id = int(data['id'])
        self.name = data['name']
        self.registration_id = int(data['registrationFormId'])
        
    def __repr__(self):
        return "<Survey(id={}, name={}, registration_id={})>".format(
            self.id, self.name, self.registration_id)

class Forms(Base):
    
    __tablename__ = "form"
    
    id = Column(Integer, primary_key=True)
    survey_id = Column(Integer)
    name = Column(Text)
    
    def __init__(self, data):
        self.id = int(data['id'])
        self.survey_id = int(data['survey_id'])
        self.name = data['name']
    
    def __repr__(self):
        return "<Forms(id={}, survey_id={}, name={})>".format(
            self.id, self.survey_id, self.name)
        
class QuestionGroups(Base):
    
    __tablename__ = "question_group"
    
    id = Column(Integer, primary_key=True)
    form_id = Column(Integer)
    repeat = Column(Boolean)
    name = Column(Text)
    
    def __init__(self, data):
        self.id = int(data['id'])
        self.form_id = int(data['form_id'])
        self.repeat = data['repeatable']
        self.name = data['name']
    
    def __repr__(self):
        return "<QuestionGroups(id={}, form_id={}, repeat={}, name={})>".format(
            self.id, self.form_id, self.repeat, self.name)
        
class Questions(Base):
    
    __tablename__ = "question"
    
    id = Column(Integer, primary_key=True)
    form_id = Column(Integer)
    question_group_id = Column(Integer)
    name = Column(Text)
    type = Column(Text)
    
    def __init__(self, data):
        self.id = int(data['id'])
        self.form_id = int(data['form_id'])
        self.question_group_id = int(data['group_id'])
        self.name = data['name']
        self.type = data['type']
    
    def __repr__(self):
        return "<Questions(id={}, form_id={}, question_group_id={}, name={}, type={})>".format(
            self.id, self.form_id, self.question_group_id, self.name, self.type)
    
class DataPoints(Base):
    
    __tablename__ = "datapoint"
    
    id = Column(Integer, primary_key=True)
    identifier = Column(Text)
    form_id = Column(Integer)
    submitter = Column(Text)
    survey_time = Column(Integer)
    
    def __init__(self, data):
        self.id = int(data['id'])
        self.identifier = data['identifier']
        self.form_id = int(data['formId'])
        self.submitter = data['submitter']
        self.survey_time = data['surveyalTime']
    
    def __repr__(self):
        return "<DataPoints(id={}, identifier={}, form_id={}, submitter={}, survey_time={})>".format(
            self.id, self.identifier, self.form_id, self.submitter, self.survey_time)

class Answers(Base):
    
    __tablename__ = "answer"
    
    id = Column(Integer, primary_key=True, autoincrement=True)
    datapoint_id = Column(Integer)
    question_id = Column(Integer)
    value = Column(Text)
    
    def __init__(self, data):
        self.datapoint_id = int(data['datapoint_id'])
        self.question_id = int(data['question_id'])
        self.value = str(data['value'])
        
    def __repr__(self):
        return "<Answers(datapoint_id={}, question_id={}, value={})>".format(
            self.datapoint_id, self.question_id, self.value)

In [9]:
def writeData(input_data, info, log):
    try:
        session.add(input_data)
        if log:
            print('INSERTING: {}'.format(log))
        session.commit()
    except:
        if log:
            print('ERROR: ABORTING {}'.format(log))
        session.rollback()
        raise

## Main Function

In [10]:
def getFolders(items):
    for folder in items['folders']:
        try:
            surveysUrl.append(folder['surveysUrl'])
            childs = Flow.getResponse(folder['foldersUrl'])
            getFolders(childs)
        except:
            pass
        
print('GETTING FOLDER LIST: ' + getTime())
parents = Flow.getResponse(requestURI + '/folders')
getFolders(parents)
print('FOLDER IS POPULATED: ' + getTime())

GETTING FOLDER LIST: 0 Minutes, 0 Seconds
FOLDER IS POPULATED: 0 Minutes, 27 Seconds


In [11]:
surveys = []
print('GETTING SURVEY LIST: ' + getTime())
for surveyUrl in surveysUrl:
    surveyList = Flow.getResponse(surveyUrl)
    for survey in surveyList['surveys']:
        surveys.append(survey)
print('SURVEY IS POPULATED: ' + getTime())

GETTING SURVEY LIST: 0 Minutes, 27 Seconds
SURVEY IS POPULATED: 0 Minutes, 52 Seconds


In [12]:
print('RECORDING SURVEY: ' + getTime())
formInstanceUrls = []
for url in surveys:
    data = Flow.getResponse(url['surveyUrl'])
    print('GETTING {}: {}'.format(data['name'],getTime()))
    if data['registrationFormId'] == "":
        data.update({'registrationFormId':0})
    input_data = Surveys(data)
    writeData(input_data, data, "SURVEY")
    for form in data['forms']:
        form.update({'survey_id':data['id']})
        input_data = Forms(form)
        writeData(input_data, form, False)
        for qgroup in form['questionGroups']:
            qgroup.update({'form_id':form['id']})
            input_data = QuestionGroups(qgroup)
            writeData(input_data, qgroup, False)
            for question in qgroup['questions']:
                question.update({'group_id':qgroup['id']})
                question.update({'form_id':form['id']})
                input_data = Questions(question)
                writeData(input_data, question, False)
        formInstanceUrls.append({
            'formInstancesUrl': form['formInstancesUrl'],
            'form_id': form['id']
        })
print('SURVEY IS RECORDED: ' + getTime())

RECORDING SURVEY: 0 Minutes, 52 Seconds
GETTING FICHE D'ENQUETE TECHNIQUE DU POINT D'EAU: 0 Minutes, 54 Seconds
INSERTING: SURVEY
GETTING Distribution équipements: 0 Minutes, 56 Seconds
INSERTING: SURVEY
GETTING Fiche d'enquête énergie copy: 0 Minutes, 58 Seconds
INSERTING: SURVEY
GETTING Questions points de vente: 1 Minutes, 0 Seconds
INSERTING: SURVEY
GETTING Fiche d'enquête énergie: 1 Minutes, 2 Seconds
INSERTING: SURVEY
GETTING Enquete Genre et Pro-poor: 1 Minutes, 3 Seconds
INSERTING: SURVEY
GETTING FICHE D'ENQUETE TECHNIQUE DU POINT D'EAU: 1 Minutes, 7 Seconds
INSERTING: SURVEY
GETTING FICHE D'ENQUETE MENAGES: 1 Minutes, 7 Seconds
INSERTING: SURVEY
GETTING Enregistrement carte: 1 Minutes, 11 Seconds
INSERTING: SURVEY
GETTING Association stickers: 1 Minutes, 12 Seconds
INSERTING: SURVEY
GETTING R2020 Commune MODELE: 1 Minutes, 15 Seconds
INSERTING: SURVEY
GETTING R2020 Commune DANOU: 1 Minutes, 17 Seconds
INSERTING: SURVEY
GETTING Suivi des pompes: 1 Minutes, 19 Seconds
INSERTING:

In [13]:
print('GETTING DATAPOINTS: ' + getTime())
for data in formInstanceUrls:
    formInstances = Flow.getResponse(data['formInstancesUrl'])
    formInstancesData = formInstances['formInstances']
    while 'nextPageUrl' in formInstances:
        nextPageData = Flow.getResponse(formInstances['nextPageUrl'])
        formInstancesData += nextPageData['formInstances']
        formInstances = nextPageData
    for datapoint in formInstancesData:
        input_data = DataPoints(datapoint)
        writeData(input_data, datapoint, "DATAPOINT")
        answers = datapoint['responses']
        for group_id in [*answers]:
            for group in answers[group_id]:
                for qid in [*group]:
                    question = getter.query(Questions).filter(Questions.id == int(qid)).first()
                    answer_value = FlowHandler(group, qid, question.type)
                    answer_value = str(answer_value)
                    answer = {
                        'datapoint_id': datapoint['id'],
                        'question_id': qid,
                        'value': answer_value
                    }
                    input_data = Answers(answer)
                    writeData(input_data, answer, answer_value)
print('DATAPOINTS RECORDED: ' + getTime())

GETTING DATAPOINTS: 1 Minutes, 38 Seconds
INSERTING: DATAPOINT
INSERTING: test
INSERTING: test
INSERTING: Fontainier
INSERTING: test
INSERTING: 0.0
INSERTING: 2019-10-22T12:59:07.368Z
INSERTING: Rouge
INSERTING: test
INSERTING: test
INSERTING: Famoco|Carte de connexion|Radio Nogema|Clé USB|Chargeur solaire|Powerbank
INSERTING: test
INSERTING: UDUMA
INSERTING: DATAPOINT
INSERTING: Salif Togola
INSERTING: Fontainier
INSERTING: Kalidi Koné
INSERTING: 99270665.0
INSERTING: 2019-11-15T11:02:54.813Z
INSERTING: G8C
INSERTING: Famoco|Chargeur solaire|Powerbank
INSERTING: Salif Togola
INSERTING: UDUMA
INSERTING: DATAPOINT
INSERTING: MAHAMADOU
INSERTING: Fontainier
INSERTING: SAMAKE
INSERTING: 0.0
INSERTING: 2019-10-18T09:19:16.948Z
INSERTING: K8S
INSERTING: Famoco|Chargeur solaire|Powerbank
INSERTING: MOHAMADIU TOGOLA
INSERTING: UDUMA
INSERTING: DATAPOINT
INSERTING: Fousseni KONE
INSERTING: Fontainier
INSERTING: Zoumana COULIBALY
INSERTING: 72375374.0
INSERTING: 2019-12-17T13:20:07.965Z
INSERTI

INSERTING: youssouf sidibe
INSERTING: UDUMA
INSERTING: DATAPOINT
INSERTING: Bintou Traoré
INSERTING: Fontainier
INSERTING: Justin Koné
INSERTING: 76815642.0
INSERTING: 2019-12-19T13:05:48.033Z
INSERTING: HU3
INSERTING: Famoco|Chargeur solaire|Powerbank
INSERTING: Bintou Traoré
INSERTING: UDUMA
INSERTING: DATAPOINT
INSERTING: Nanbi Koné
INSERTING: Fontainier
INSERTING: Kalidi Koné
INSERTING: 93432928.0
INSERTING: 2019-11-05T13:19:59.230Z
INSERTING: HPZ
INSERTING: Famoco|Chargeur solaire|Powerbank
INSERTING: Nanbi Koné
INSERTING: UDUMA
INSERTING: DATAPOINT
INSERTING: Youba Koné
INSERTING: Fontainier
INSERTING: Kalidi Koné
INSERTING: 73703522.0
INSERTING: 2019-11-05T13:10:40.106Z
INSERTING: G8D
INSERTING: Famoco|Chargeur solaire|Powerbank
INSERTING: Youba Koné
INSERTING: UDUMA
INSERTING: DATAPOINT
INSERTING: SEYDOU TOGOLA
INSERTING: Fontainier
INSERTING: SAMAKE
INSERTING: 75506236.0
INSERTING: 2019-12-07T11:06:57.448Z
INSERTING: K8Q
INSERTING: Famoco|Chargeur solaire|Powerbank
INSERTING: 

INSERTING: DATAPOINT
INSERTING: [11.22320817, -8.23818739]
INSERTING: 78084847.0
INSERTING: Zile Diakite
INSERTING: YANFOLILA:YANFOLILA|WASSOULOU-BALLE:WASSOULOU-BALLE|GOUALALA 2:GOUALALA 2
INSERTING: épicerie
INSERTING: DATAPOINT
INSERTING: [10.94003738, -8.23277755]
INSERTING: 93547422.0
INSERTING: Chacka Sidibe
INSERTING: YANFOLILA:YANFOLILA|WASSOULOU-BALLE:WASSOULOU-BALLE|KARATOU:KARATOU
INSERTING: épicerie
INSERTING: DATAPOINT
INSERTING: [11.54786565, -6.84222844]
INSERTING: bourama togola
INSERTING: BOUGOUNI:BOUGOUNI|KOUMANTOU:KOUMANTOU|KOLA:KOLA
INSERTING: vente des pieces velo moto
INSERTING: DATAPOINT
INSERTING: [11.44519054, -6.65660207]
INSERTING: 60308310.0
INSERTING: Soumaïla Doumbia
INSERTING: BOUGOUNI:BOUGOUNI|KOUMANTOU:KOUMANTOU|TIEFALA:TIEFALA
INSERTING: Boutique Divers
INSERTING: DATAPOINT
INSERTING: [11.23514561, -6.97123758]
INSERTING: 77870860.0
INSERTING: Arouna Diallo
INSERTING: KOLONDIEBA:KOLONDIEBA|KEBILA:KEBILA|MASSALA:MASSALA
INSERTING: épicerie
INSERTING: DA

INSERTING: Oui, radio avec piles rechargeables
INSERTING: Moto
INSERTING: 1000.0
INSERTING: Non
INSERTING: 76936994.0
INSERTING: BOUGOUNI:BOUGOUNI|KELEYA:KELEYA|SEMANA:SEMANA
INSERTING: Moussa Traore
INSERTING: [11.84647559, -7.59381928]
INSERTING: 13.0
INSERTING: Dans le quartier
INSERTING: 30 - 60 minutes
INSERTING: 4.0
INSERTING: Oui
INSERTING: Autre
INSERTING: 6
INSERTING: 0.0
INSERTING: Non
INSERTING: Hors du village
INSERTING: Bois
INSERTING: 0.0
INSERTING: Non
INSERTING: DATAPOINT
INSERTING: Mahamadou Doumbia
INSERTING: [11.55326654, -7.06408338]
INSERTING: 16.0
INSERTING: 65018048.0
INSERTING: Sounsounkoro2
INSERTING: BOUGOUNI:BOUGOUNI|DEBELIN:DEBELIN|SOUNSOUNKORO 2:SOUNSOUNKORO 2
INSERTING: Dans le quartier
INSERTING: Oui
INSERTING: Voir des connaissances
INSERTING: 5
INSERTING: 100.0
INSERTING: entre 60 et 90 minutes
INSERTING: 1.0
INSERTING: Bois
INSERTING: 0.0
INSERTING: Hors du village
INSERTING: Regarder la télévision nationale
INSERTING: https://akvoflow-166.s3.amazonaws

INSERTING: [11.14235108, -8.31208225]
INSERTING: 13.0
INSERTING: 75394794.0
INSERTING: Téléby
INSERTING: YANFOLILA:YANFOLILA|WASSOULOU-BALLE:WASSOULOU-BALLE|SEKOU:SEKOU
INSERTING: Seydou Diakite
INSERTING: 500.0
INSERTING: Oui
INSERTING: 1500.0
INSERTING: Moto
INSERTING: Dans le village
INSERTING: Bois
INSERTING: 1500.0
INSERTING: DATAPOINT
INSERTING: 60308310.0
INSERTING: BOUGOUNI:BOUGOUNI|KOUMANTOU:KOUMANTOU|TIEFALA:TIEFALA
INSERTING: solomane doumbia
INSERTING: [11.44569501, -6.65760824]
INSERTING: 6.0
INSERTING: 0.0
INSERTING: A la maison
INSERTING: Elle fonctionne toujours
INSERTING: 300.0
INSERTING: https://akvoflow-166.s3.amazonaws.com/images/cbd612ea-261e-4721-9f5d-5ec96473e8e4.jpg
INSERTING: 1.0
INSERTING: 300.0
INSERTING: 15.0
INSERTING: Une fois toutes les 2 semaines
INSERTING: 2.0
INSERTING: Oui, radio avec piles non-rechargeables|Oui, radio sur batterie externe rechargeable
INSERTING: Non
INSERTING: Bois
INSERTING: 500.0
INSERTING: Hors du village
INSERTING: Oui
INSERTING:

...

INSERTING: Remplacer la pompe India par une e-pompe VHY complète
INSERTING: India
INSERTING: Test de qualité eau pas effectué, les usagers disent que la qualité est mauvaise
INSERTING: Eau claire, pas de sable
INSERTING: [11.421563333333332, -6.7829033333333335]
INSERTING: Oui
INSERTING: Poser un nouveau cadre à sceller
INSERTING: Piqueter le béton en surface et créer une margelle de 10 cm d’épaisseur minimum
INSERTING: Faire à neuf 2 marchepieds
INSERTING: Boucher les fissures de la dalle et refaire le béton autour de la margelle
INSERTING: Pompe India Mark à retirer pour installation d'une e-pompe VHY
INSERTING: DATAPOINT
INSERTING: Faire un marchepied pour pompe India
INSERTING: Pompe India Mark à conserver et ajout d’une borne de comptage
INSERTING: Boucher les fissures de la dalle et refaire le béton autour de la margelle
INSERTING: Piqueter le béton en surface et créer une margelle à minima
INSERTING: Casser une partie de l'enclos de la superstructure|Prolonger la margelle pour p

INSERTING: 24.0
INSERTING: [11.45780252, -7.00094979]
INSERTING: Oui
INSERTING: DATAPOINT
INSERTING: 1.35
INSERTING: 22.0
INSERTING: [11.458723333333333, -7.00422]
INSERTING: Oui
INSERTING: Oui, pas de sable visible
INSERTING: 50.92
INSERTING: 2.3
INSERTING: DATAPOINT
INSERTING: 1.12
INSERTING: 23.8
INSERTING: [11.445158333333332, -6.659016666666668]
INSERTING: Oui
INSERTING: Oui, pas de sable visible
INSERTING: 51.24
INSERTING: 3.38
INSERTING: DATAPOINT
INSERTING: Pose d'un nouveau cadre à sceller
INSERTING: Pas de marchepieds présent, fabrication 2 marchepieds neufs
INSERTING: Pas de margelle présente, fabrication margelle neuve selon le plan
INSERTING: Pompe à retirer pour installation d'une e-pompe VHY
INSERTING: Bouché les fissures de la dalle restauration du béton autour de la margelle|Amélioré le bon évacuation de l'eau
INSERTING: Non
INSERTING: 15.0
INSERTING: [11.40300533, -7.01971087]
INSERTING: Oui
INSERTING: Oui, pas de sable visible
INSERTING: 32.23
INSERTING: 0.97
INSERTI

INSERTING: Pas de marchepieds présent, fabrication 2 marchepieds neufs
INSERTING: Pas de margelle présente, fabrication margelle neuve selon le plan
INSERTING: https://akvoflow-166.s3.amazonaws.com/images/fa9c3f04-4ae9-4a18-9a9f-db8491e1a9a9.jpg
INSERTING: 2019-10-23T14:16:02.362Z
INSERTING: Installation e-pompe VHY complète
INSERTING: https://akvoflow-166.s3.amazonaws.com/images/3c5758c4-6c2b-4e8f-a110-4a0657b8ae2b.jpg
INSERTING: Non
INSERTING: Pas indiqué par le Conducteur de Travaux
INSERTING: 10.0
INSERTING: [11.39943333333333, -7.0196499999999995]
INSERTING: Non
INSERTING: DATAPOINT
INSERTING: Ancien cadre à sceller préservé, reserré les écrous
INSERTING: Casse ancien(s) marchepied(s), fabrication 2 marchepieds neufs
INSERTING: Pas de margelle présente, fabrication margelle neuve selon le plan
INSERTING: Pompe à retirer pour installation d'une e-pompe VHY
INSERTING: Bouché les fissures de la dalle restauration du béton autour de la margelle|Amélioré le bon évacuation de l'eau
INSE

INSERTING: https://akvoflow-166.s3.amazonaws.com/images/0b546abf-f21b-4350-8d8e-46dac53dbdf7.jpg
INSERTING: Non
INSERTING: https://akvoflow-166.s3.amazonaws.com/images/5518bdd9-21e1-4642-8d31-f1bb83d2eeef.jpg
INSERTING: DATAPOINT
INSERTING: 1.3
INSERTING: 10.0
INSERTING: [11.458995, -7.002355]
INSERTING: Oui
INSERTING: Oui, tâche de sable de moins de 1cm
INSERTING: 0.27
INSERTING: DATAPOINT
INSERTING: 2019-10-07T15:35:34.844Z
INSERTING: Installation borne compteur sur India
INSERTING: https://akvoflow-166.s3.amazonaws.com/images/c4880a66-614e-4cb8-b128-3e6201579936.jpg
INSERTING: Oui
INSERTING: https://akvoflow-166.s3.amazonaws.com/images/570ed08b-1ab1-4ba6-8d35-97f9fb5f9fe5.jpg
INSERTING: [11.444733333333334, -6.654566666666667]
INSERTING: Non
INSERTING: pompe india neuve, eau claire, pas de sable
INSERTING: Fabrication d'un marchepied pour India
INSERTING: Pompe India à conserver pour installation d'une borne comptage
INSERTING: Pas de dalle présente, fabrication dalle à minima|Stabl

INSERTING: Oui, pas de sable visible
INSERTING: 68.55
INSERTING: 5.77
INSERTING: DATAPOINT
INSERTING: Pose d'un nouveau cadre à sceller
INSERTING: Pas de marchepieds présent, fabrication 2 marchepieds neufs
INSERTING: Pas de margelle présente, fabrication margelle neuve selon le plan
INSERTING: Pompe à retirer pour installation d'une e-pompe VHY
INSERTING: Bouché les fissures de la dalle restauration du béton autour de la margelle|Amélioré le bon évacuation de l'eau
INSERTING: Non
INSERTING: 24.0
INSERTING: [11.348035000000001, -6.717438333333333]
INSERTING: Oui
INSERTING: Oui, tâche de sable de moins de 1cm
INSERTING: 40.92
INSERTING: 2019-10-19T10:50:10.449Z
INSERTING: Installation e-pompe VHY complète
INSERTING: https://akvoflow-166.s3.amazonaws.com/images/151ba30a-e654-4d29-b1be-562aa2e025e8.jpg
INSERTING: Non
INSERTING: https://akvoflow-166.s3.amazonaws.com/images/85b8cba9-7c8d-40dc-a33e-269ab4bb8451.jpg
INSERTING: DATAPOINT
INSERTING: 1.16
INSERTING: 20.54
INSERTING: [11.44735333

In [14]:
session.rollback()

In [15]:
total_surveys = session.query(Surveys).count()
total_forms = session.query(Forms).count()
total_question_groups = session.query(QuestionGroups).count()
total_questions = session.query(Questions).count()
total_datapoints = session.query(DataPoints).count()

In [16]:
print(
    'SUCCESS : {}\n\n'\
    '{} SURVEYS\n'\
    '{} FORMS\n'\
    '{} QUESTION GROUPS\n'\
    '{} QUESTIONS\n'\
    '{} DATAPOINTS\n'\
    .format(getTime(),total_surveys,total_forms,total_question_groups,total_questions, total_datapoints)
)

SUCCESS : 31 Minutes, 47 Seconds

22 SURVEYS
48 FORMS
93 QUESTION GROUPS
905 QUESTIONS
11685 DATAPOINTS



In [18]:
session.query(Answers).count()

205494